# Train Text Classification Model and Save to Mlflow

## I) Train Model

In [1]:
import sklearn
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.svm import LinearSVC
from bs4 import BeautifulSoup
import re
import numpy as np

In [2]:
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords, wordnet
import nltk
nltk.download('averaged_perceptron_tagger')
nltk.download('wordnet')
nltk.download('stopwords')
nltk.download('omw')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/christian/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/christian/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/christian/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package omw to /Users/christian/nltk_data...
[nltk_data]   Package omw is already up-to-date!


True

In [3]:
from sklearn.datasets import fetch_20newsgroups

In [4]:

# sklearn transformer for pipeline
class peprocessor(BaseEstimator, TransformerMixin):
    
    """text preprocessor"""

    def __init__(self):
        self.lemmatizer = WordNetLemmatizer()
        self.nltk_stopwords = stopwords.words('english')

    def nltk_tag_to_wordnet_tag(self, nltk_tag):
        if nltk_tag.startswith('J'):
            return wordnet.ADJ
        elif nltk_tag.startswith('V'):
            return wordnet.VERB
        elif nltk_tag.startswith('N'):
            return wordnet.NOUN
        elif nltk_tag.startswith('R'):
            return wordnet.ADV
        else:          
            return wordnet.NOUN

    def remove_html_tags(self, text):
        soup = BeautifulSoup(text, "html.parser")
        removed_html_text = soup.get_text()
        return removed_html_text

    def remove_special_chars(self, text):

        pattern = r'[^a-zA-z0-9\s]'
        text = re.sub(pattern, '', text)
        text = re.sub(r'[\x00-\x08\x0b\x0c\x0e-\x1f\x7f-\xff]', '', text)
        return text

    def preprocess_doc(self, text):
        
        print('preprocess doc ', text)

        assert type(text) == str

        text = text.replace(r'\n',' ')

        text = self.remove_html_tags(text)

        text = self.remove_special_chars(text)
        print("after prepro ", text)

        if len(text.split()) < 5:
            return np.nan

        # tokenize the sentence and find the POS tag for each token
        nltk_tagged = nltk.pos_tag(nltk.word_tokenize(text))
        
        # tuple of (token, wordnet_tag)
        wordnet_tagged = map(lambda x: (x[0], self.nltk_tag_to_wordnet_tag(
                    x[1])), nltk_tagged)    
        lemmas = [self.lemmatizer.lemmatize(word, tag) for word, tag in \
                wordnet_tagged if not word in self.nltk_stopwords]
        
        return lemmas

    def transform(self, X, y=None):
        return [self.preprocess_doc(text) for text in X]
    def fit(self, X, y=None):
        return self    


In [5]:
preproc = peprocessor()

### Data Prep

In [6]:
newsgroups_train = fetch_20newsgroups(subset='train', categories=['alt.atheism', 'sci.space'],
                                     random_state=42)

In [7]:
X = newsgroups_train.data
y = newsgroups_train.target

In [8]:
X[0]

'From: bil@okcforum.osrhe.edu (Bill Conner)\nSubject: Re: Not the Omni!\nNntp-Posting-Host: okcforum.osrhe.edu\nOrganization: Okcforum Unix Users Group\nX-Newsreader: TIN [version 1.1 PL6]\nLines: 18\n\nCharley Wingate (mangoe@cs.umd.edu) wrote:\n: \n: >> Please enlighten me.  How is omnipotence contradictory?\n: \n: >By definition, all that can occur in the universe is governed by the rules\n: >of nature. Thus god cannot break them. Anything that god does must be allowed\n: >in the rules somewhere. Therefore, omnipotence CANNOT exist! It contradicts\n: >the rules of nature.\n: \n: Obviously, an omnipotent god can change the rules.\n\nWhen you say, "By definition", what exactly is being defined;\ncertainly not omnipotence. You seem to be saying that the "rules of\nnature" are pre-existant somehow, that they not only define nature but\nactually cause it. If that\'s what you mean I\'d like to hear your\nfurther thoughts on the question.\n\nBill\n'

In [9]:
y[0]

0

In [10]:
len(X), len(y)

(1073, 1073)

### Feature Engineering

Create tokens in prepro step, hence pass tokens to tfidf vect.

In [11]:
X_prepro = [preproc.preprocess_doc(text) for text in X]

preprocess doc  From: bil@okcforum.osrhe.edu (Bill Conner)
Subject: Re: Not the Omni!
Nntp-Posting-Host: okcforum.osrhe.edu
Organization: Okcforum Unix Users Group
X-Newsreader: TIN [version 1.1 PL6]
Lines: 18

Charley Wingate (mangoe@cs.umd.edu) wrote:
: 
: >> Please enlighten me.  How is omnipotence contradictory?
: 
: >By definition, all that can occur in the universe is governed by the rules
: >of nature. Thus god cannot break them. Anything that god does must be allowed
: >in the rules somewhere. Therefore, omnipotence CANNOT exist! It contradicts
: >the rules of nature.
: 
: Obviously, an omnipotent god can change the rules.

When you say, "By definition", what exactly is being defined;
certainly not omnipotence. You seem to be saying that the "rules of
nature" are pre-existant somehow, that they not only define nature but
actually cause it. If that's what you mean I'd like to hear your
further thoughts on the question.

Bill

after prepro  From bilokcforumosrheedu Bill Conner
Su

preprocess doc  From: healta@saturn.wwc.edu (Tammy R Healy)
Subject: Cannanite genocide in the Bible
Lines: 6
Organization: Walla Walla College
Lines: 6

excuse me for my ignorance. But I remember reading once that the 
Biblical tribe known as the Philistines still exists...they are the modern 
day Palestinians.
Anyone out there with more info, please post it!!!

Tammy

after prepro  From healtasaturnwwcedu Tammy R Healy
Subject Cannanite genocide in the Bible
Lines 6
Organization Walla Walla College
Lines 6

excuse me for my ignorance But I remember reading once that the 
Biblical tribe known as the Philistines still existsthey are the modern 
day Palestinians
Anyone out there with more info please post it

Tammy

preprocess doc  From: bil@okcforum.osrhe.edu (Bill Conner)
Subject: Re: Second Law (was: Albert Sabin)
Nntp-Posting-Host: okcforum.osrhe.edu
Organization: Okcforum Unix Users Group
X-Newsreader: TIN [version 1.1 PL6]
Lines: 20

Joel Hanes (jjh00@diag.amdahl.com) wrote:

: Mr

preprocess doc  From: livesey@solntze.wpd.sgi.com (Jon Livesey)
Subject: Re: Slavery (was Re: Why is sex only allowed in marriage: ...)
Organization: sgi
Lines: 37
Distribution: world
NNTP-Posting-Host: solntze.wpd.sgi.com

In article <1993Apr15.081303.16532@Cadence.COM>, mas@Cadence.COM (Masud Khan) writes:
|> 
|> Leonard, I'll give you an example of this....
|> 
|> My father recently bought a business, the business price was 150,000 pounds
|> and my father approached the people in the community for help, he raised
|> 60,000 pounds in interest free loans from friends and relatives and 
|> Muslims he knew, 50,000 had cash and the rest he got a business loan, after
|> paying off the Muslim lenders many of them helped him with further loans
|> to help him clear the bank debt and save him from further intrest, this
|> is an example of a Muslim community helping one another, why did they help
|> because of their common identity as Muslims. In turn my father has helped
|> with people buying

preprocess doc  From: madhaus@netcom.com (Maddi Hausmann)
Subject: Re: Amusing atheists and agnostics
Organization: Society for Putting Things on Top of Other Things
Lines: 40

timmbake@mcl.ucsb.edu (Bake Timmons) writes: >

>OK, you have disproved one thing, but you failed to "nail" me.
>
>See, nowhere in my post did I claim that something _must_ be believed in.  Here
>are the three possibilities:
>
>	1) God exists. 
>	2) God does not exist.
>	3) I don't know.
>
>My attack was on strong atheism, (2).  Since I am (3), I guess by what you said
>below that makes me a weak atheist.
  [snip]
>First of all, you seem to be a reasonable guy.  Why not try to be more honest
>and include my sentence afterwards that 

Honest, it just ended like that, I swear!  

Hmmmm...I recognize the warning signs...alternating polite and
rude...coming into newsgroup with huge chip on shoulder...calls
people names and then makes nice...whirrr...click...whirrr

"Clam" Bake Timmons = Bill "Shit Stirrer Connor"

Q

preprocess doc  From: jaeger@buphy.bu.edu (Gregg Jaeger)
Subject: Re: The Inimitable Rushdie
Organization: Boston University Physics Department
Lines: 27

In article <1qlb7oINN684@shelley.u.washington.edu> 
jimh@carson.u.washington.edu (James Hogan) writes:


>20:52 P.S.T.  I come to my senses and accept the all-knowing
>wisdom and power of the Quran and Allah.  Not only that, but Allah 
>himself drops by to congratulate me on my wise choice. Allah rolls a
>few bones and we get down.  Then Allah gets out the Crisco, bends 
>over, and invites me to take a spin around the block.  Wow.


>20:56 P.S.T.  I realize that maybe Allah is looking for more of a 
>commitment than I'm ready for, so I say "Man, I've got some
>programming to do.  Gotta go.  I'll call you."


>20:59 P.S.T   Thinking it over, I renounce Islam.

What loyalty!

Jim, it seems you've been reading a little too much Russell Hoban
lately. As Hemingway said, my imitators always imitate the _bad_
aspects of my writing. Hoban wo

...

preprocess doc  From: bobbe@vice.ICO.TEK.COM (Robert Beauchaine)
Subject: Re: "Cruel" (was Re: <Political Atheists?)
Organization: Tektronix Inc., Beaverton, Or.
Lines: 20

In article <1ql8mdINN674@gap.caltech.edu> keith@cco.caltech.edu (Keith Allan Schneider) writes:
>
>But we were discussing it in relation to the death penalty.  And, the
>Constitution need not define each of the words within.  Anyone who doesn't
>know what cruel is can look in the dictionary (and we did).
>

  Or, with no dictionary available, they could gain first hand
  knowledge by suffering through one of your posts.


/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\/\ 

Bob Beauchaine bobbe@vice.ICO.TEK.COM 

They said that Queens could stay, they blew the Bronx away,
and sank Manhattan out at sea.

^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^


after prepro  From bobbeviceICOTEKCOM Robert Beauchaine
Subject Re Cruel was Re  keithccocaltechedu Keith Allan Schneider write

after prepro  Subject Re Yet more Rushdie [Re ISLAMIC LAW]
From kmr4poCWRUedu Keith M Ryan
Organization Case Western Reserve University
NNTPPostingHost b64635studentcwruedu
Lines 27

In article 1993Apr615184315240monu6ccmonasheduau dariceyoyoccmonasheduau Fred Rice writes
I should clarify what Muslims usually mean when they say Muslim  In
general anyone who calls themselves a Muslim and does not do or 
outwardly profess
something in clear contradiction with the essential teachings of Islam
is considered to be a Muslim  Thus one who might do things contrary to
Islam through ignorance for example does not suddenly _not_ become a
Muslim  If one knowingly transgresses Islamic teachings and essential
principles though then one does leave Islam

	You and Mr bobby really need to sit down and decide what
exactly Islam  is before posting here

	According to Zlumber one is NOT a muslim when one is doing evil 
[ A muslin can do no evil ] According to him one who does evil is suffering 
from tempo

preprocess doc  From: keith@cco.caltech.edu (Keith Allan Schneider)
Subject: Re: <Political Atheists?
Organization: California Institute of Technology, Pasadena
Lines: 76
NNTP-Posting-Host: lloyd.caltech.edu

kcochran@nyx.cs.du.edu (Keith "Justified And Ancient" Cochran) writes:

>>>How many contridictions do you want to see?
>>Good question. If I claim something is a general trend, then to disprove this,
>>I guess you'd have to show that it was not a general trend.
>No, if you're going to claim something, then it is up to you to prove it.
>Think "Cold Fusion".

Well, I've provided examples to show that the trend was general, and you
(or others) have provided some counterexamples, mostly ones surrounding
mating practices, etc.  I don't think that these few cases are enough to
disprove the general trend of natural morality.  And, again, the mating
practices need to be reexamined...

>>Try to find "immoral" non-mating-related activities.
>So you're excluding mating-related-activities fro

preprocess doc  From: rdl1@ukc.ac.uk (R.D.Lorenz)
Subject: Cold Gas tanks for Sounding Rockets
Organization: Computing Lab, University of Kent at Canterbury, UK.
Lines: 14
Nntp-Posting-Host: eagle.ukc.ac.uk

>Does anyone know how to size cold gas roll control thruster tanks
>for sounding rockets?

Well, first you work out how much cold gas you need, then make the
tanks big enough.

Working out how much cold gas is another problem, depending on
vehicle configuration, flight duration, thruster Isp (which couples
into storage pressure, which may be a factor in selecting tank
wall thickness etc.)

Ralph Lorenz
Unit for Space Sciences
University of Kent, UK

after prepro  From rdl1ukcacuk RDLorenz
Subject Cold Gas tanks for Sounding Rockets
Organization Computing Lab University of Kent at Canterbury UK
Lines 14
NntpPostingHost eagleukcacuk

Does anyone know how to size cold gas roll control thruster tanks
for sounding rockets

Well first you work out how much cold gas you need then make the

preprocess doc  From: bcash@crchh410.NoSubdomain.NoDomain (Brian Cash)
Subject: Re: New Member
Nntp-Posting-Host: crchh410
Organization: BNR, Inc.
Lines: 47

In article <C5HIEw.7s1@portal.hq.videocart.com>, dfuller@portal.hq.videocart.com (Dave Fuller) writes:
|>   Hello. I just started reading this group today, and I think I am going
|> to be a large participant in its daily postings. I liked the section of
|> the FAQ about constructing logical arguments - well done. I am an atheist,
|> but I do not try to turn other people into atheists. I only try to figure
|> why people believe the way they do - I don't much care if they have a 
|> different view than I do. When it comes down to it . . . I could be wrong.
|> I am willing to admit the possibility - something religious followers 
|> dont seem to have the capability to do.

Welcome aboard!

|> 
|>   I notice alot of posts from Bobby. Why does anybody ever respond to 
|> his posts ? He always falls back on the same argument:

(I think 

In [12]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [13]:
def identity_tokenizer(text):
    return text
tfidf_vec = TfidfVectorizer(lowercase=False, tokenizer=identity_tokenizer, stop_words=None)

In [14]:
from sklearn.pipeline import Pipeline

In [15]:
X_feat = tfidf_vec.fit_transform(X_prepro)

In [16]:
X_feat

<1073x25528 sparse matrix of type '<class 'numpy.float64'>'
	with 147153 stored elements in Compressed Sparse Row format>

### Training

In [17]:
pipe = Pipeline([
    ('prepro', peprocessor()),
    ('tfidf', tfidf_vec),
    ('clf', LinearSVC(class_weight = 'balanced', random_state=42))
])

In [18]:
pipe.fit(X[:5], y[:5])

preprocess doc  From: bil@okcforum.osrhe.edu (Bill Conner)
Subject: Re: Not the Omni!
Nntp-Posting-Host: okcforum.osrhe.edu
Organization: Okcforum Unix Users Group
X-Newsreader: TIN [version 1.1 PL6]
Lines: 18

Charley Wingate (mangoe@cs.umd.edu) wrote:
: 
: >> Please enlighten me.  How is omnipotence contradictory?
: 
: >By definition, all that can occur in the universe is governed by the rules
: >of nature. Thus god cannot break them. Anything that god does must be allowed
: >in the rules somewhere. Therefore, omnipotence CANNOT exist! It contradicts
: >the rules of nature.
: 
: Obviously, an omnipotent god can change the rules.

When you say, "By definition", what exactly is being defined;
certainly not omnipotence. You seem to be saying that the "rules of
nature" are pre-existant somehow, that they not only define nature but
actually cause it. If that's what you mean I'd like to hear your
further thoughts on the question.

Bill

after prepro  From bilokcforumosrheedu Bill Conner
Su

Pipeline(steps=[('prepro', peprocessor()),
                ('tfidf',
                 TfidfVectorizer(lowercase=False,
                                 tokenizer=<function identity_tokenizer at 0x7f7f1cb20710>)),
                ('clf', LinearSVC(class_weight='balanced', random_state=42))])

### Evalution
Skip validation set performance evaluation. Short check on training data only for functionality test.

In [19]:
pipe.predict(X[:5])

preprocess doc  From: bil@okcforum.osrhe.edu (Bill Conner)
Subject: Re: Not the Omni!
Nntp-Posting-Host: okcforum.osrhe.edu
Organization: Okcforum Unix Users Group
X-Newsreader: TIN [version 1.1 PL6]
Lines: 18

Charley Wingate (mangoe@cs.umd.edu) wrote:
: 
: >> Please enlighten me.  How is omnipotence contradictory?
: 
: >By definition, all that can occur in the universe is governed by the rules
: >of nature. Thus god cannot break them. Anything that god does must be allowed
: >in the rules somewhere. Therefore, omnipotence CANNOT exist! It contradicts
: >the rules of nature.
: 
: Obviously, an omnipotent god can change the rules.

When you say, "By definition", what exactly is being defined;
certainly not omnipotence. You seem to be saying that the "rules of
nature" are pre-existant somehow, that they not only define nature but
actually cause it. If that's what you mean I'd like to hear your
further thoughts on the question.

Bill

after prepro  From bilokcforumosrheedu Bill Conner
Su

array([0, 1, 1, 1, 0])

## II) Save to Mlflow

Use custom pyfunc implementation due to the nltk dependency

In [20]:
from mlflow.models.signature import ModelSignature
from mlflow.types.schema import Schema, ColSpec
import mlflow

In [21]:
input_example = {
  "text": "Please enlighten me.  How is omnipotence contradictory",
}
input_schema = Schema([
  ColSpec("string", "text")
])
output_schema = Schema([ColSpec("string")])
signature = ModelSignature(inputs=input_schema, outputs=output_schema)
signature

inputs: 
  ['text': string]
outputs: 
  [string]

In [22]:
test_text = ["Please enlighten me.  How is omnipotence contradictory"]

### Save Local

In [23]:
# ! rm -rf tests/classifier
# mlflow.sklearn.save_model(
#     pipe, 
#     path = "tests/classifier", # save local
#     conda_env="environment_model.yml", 
#     #mlflow_model=None, 
#     #serialization_format='cloudpickle', 
#     signature = signature,
#     input_example = input_example, 
#     pip_requirements=None, extra_pip_requirements=None)

In [24]:
#local_model = mlflow.sklearn.load_model("classifier")

In [25]:
#local_model.predict(test_text)

### Save to MLflow

In [41]:
mlflow.set_tracking_uri("http://localhost:8088")

In [42]:
experiment_name = "document_classifier"

In [43]:
#mlflow.create_experiment(experiment_name)

In [44]:
mlflow.set_experiment(experiment_name)
experiment = mlflow.get_experiment_by_name(experiment_name)

In [45]:
mlflow.start_run(experiment_id=experiment.experiment_id, run_name="baseline3")

<ActiveRun: >

In [46]:
mlflow.sklearn.log_model(
    pipe, 
    artifact_path="model", 
    conda_env="environment_model.yml", 
    #serialization_format='cloudpickle', 
    registered_model_name=None, 
    signature= signature,
    input_example= input_example)
    #await_registration_for=300, 
    #pip_requirements=None, 
    #extra_pip_requirements=None)

In [47]:
!jupyter nbconvert --to html NLP_Classifier.ipynb
mlflow.log_artifact("NLP_Classifier.ipynb")
mlflow.log_artifact("NLP_Classifier.html")

[NbConvertApp] WARNING | Config option `template_path` not recognized by `HTMLExporter`.  Did you mean one of: `extra_template_paths, template_name, template_paths`?
[NbConvertApp] Converting notebook NLP_Classifier.ipynb to html
[NbConvertApp] Writing 5080941 bytes to NLP_Classifier.html


In [48]:
mlflow.end_run()